In [1]:
!trtexec

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec
=== Model Options ===
  --uff=<file>                UFF model
  --onnx=<file>               ONNX model
  --model=<file>              Caffe model (default = no model, random weights used)
  --deploy=<file>             Caffe prototxt file
  --output=<name>[,<name>]*   Output names (it can be specified multiple times); at least one output is required for UFF and Caffe
  --uffInput=<name>,X,Y,Z     Input blob name and its dimensions (X,Y,Z=C,H,W), it can be specified multiple times; at least one is required for UFF models
  --uffNHWC                   Set if inputs are in the NHWC layout instead of NCHW (use X,Y,Z=H,W,C order in --uffInput)

=== Build Options ===
  --maxBatch                  Set max batch size and build an implicit batch engine (default = same size as --batch)
                              This option should not be used when the input model is ONNX or when dynamic shapes are provided.
  --minShapes=spec            B

In [2]:
import os

In [3]:
ONNX_MODEL_DIR = './Flask/Models/'

FLASK_MODEL_DIR = './Flask/Models/'

TRITON_MODEL_DIR = './Triton/Models/'
TRITON_CONFIG_FILE = 'config.pbtxt'
TRITON_MODEL_FILE = 'model.plan'

In [4]:
def save_tensorrt_model(onnx_model, trt_model, precision, config):
    trt_model = trt_model + '_' + precision
    onnx_model_path = os.path.join(ONNX_MODEL_DIR, onnx_model + '.onnx')
    flask_model_path = os.path.join(FLASK_MODEL_DIR, trt_model + '.plan')

    !trtexec \
        --onnx=$onnx_model_path \
        --explicitBatch \
        --$precision \
        --saveEngine=$flask_model_path

    triton_config_path = os.path.join(TRITON_MODEL_DIR, trt_model, TRITON_CONFIG_FILE)
    os.makedirs(os.path.dirname(triton_config_path), exist_ok=True)
    with open(triton_config_path, 'w') as f:
        f.write(config.strip())

    triton_model_path = os.path.join(TRITON_MODEL_DIR, trt_model, '1', TRITON_MODEL_FILE)
    os.makedirs(os.path.dirname(triton_model_path), exist_ok=True)
    !cp $flask_model_path $triton_model_path
        
    print(flask_model_path)
    print(triton_config_path)
    print(triton_model_path)
    return

In [5]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/resnet34-trt_best.plan
[09/22/2022-08:48:39] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:48:39] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:48:39] [I] === Model Options ===
[09/22/2022-08:48:39] [I] Format: ONNX
[09/22/2022-08:48:39] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/22/2022-08:48:39] [I] Output:
[09/22/2022-08:48:39] [I] === Build Options ===
[09/22/2022-08:48:39] [I] Max batch: explicit batch
[09/22/2022-08:48:39] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:48:39] [I] minTiming: 1
[09/22/2022-08:48:39] [I] avgTiming: 8
[09/22/2022-08:48:39] [I] Precision: FP32+FP16+INT8
[09/22/2022-08:48:39] [I] LayerPrecisions: 
[09

[09/22/2022-08:48:49] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:49] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:49] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:49] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:48:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the wei

[09/22/2022-08:48:51] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:51] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:51] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:51] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:51] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:51] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:51] [W] [TRT] Weights [name=Conv_13 + Relu_14.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:51] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:51] [W] [TRT] If this is not the desired behavior, please modify the weights or ret

[09/22/2022-08:48:53] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:53] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:53] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:53] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:53] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:53] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:53] [W] [TRT] Weights [name=Conv_20 + Add_22 + Relu_23.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:53] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:53] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with r

[09/22/2022-08:48:56] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:56] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:56] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:56] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:56] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:56] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:48:56] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/22/2022-08:48:56] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:48:56] [W] [TRT] If this is not the desired behavior, pleas

...

[09/22/2022-08:49:04] [W] [TRT] Weights [name=Conv_70 + Relu_71.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:04] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:05] [W] [TRT] Weights [name=Conv_70 + Relu_71.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:05] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

[09/22/2022-08:49:09] [W] [TRT] Weights [name=Conv_76 + Relu_77.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:09] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:09] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:09] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:09] [W] [TRT] Weights [name=Conv_76 + Relu_77.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:09] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:09] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:09] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

[09/22/2022-08:49:13] [W] [TRT] Weights [name=Conv_81 + Relu_82.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:13] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:13] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:13] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:13] [W] [TRT] Weights [name=Conv_81 + Relu_82.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:13] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:13] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:13] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the

[09/22/2022-08:49:14] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:14] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/22/2022-08:49:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:14] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:14] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:14] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

./Flask/Models/resnet34-trt_best.plan
./Triton/Models/resnet34-trt_best/config.pbtxt
./Triton/Models/resnet34-trt_best/1/model.plan


In [6]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/resnet34-trt_fp16.plan
[09/22/2022-08:49:19] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:49:19] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:49:19] [I] === Model Options ===
[09/22/2022-08:49:19] [I] Format: ONNX
[09/22/2022-08:49:19] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/22/2022-08:49:19] [I] Output:
[09/22/2022-08:49:19] [I] === Build Options ===
[09/22/2022-08:49:19] [I] Max batch: explicit batch
[09/22/2022-08:49:19] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:49:19] [I] minTiming: 1
[09/22/2022-08:49:19] [I] avgTiming: 8
[09/22/2022-08:49:19] [I] Precision: FP32+FP16
[09/22/2022-08:49:19] [I] LayerPrecisions: 
[09/22/2

[09/22/2022-08:49:24] [W] [TRT] Weights [name=Conv_0 + Relu_1.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:24] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:24] [W] [TRT] Weights [name=Conv_0 + Relu_1.bias] had the following issues when converted to FP16:
[09/22/2022-08:49:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:24] [W] [TRT] Weights [name=Conv_3 + Relu_4.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:24] [W] [

[09/22/2022-08:49:25] [W] [TRT] Weights [name=Conv_8 + Relu_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:25] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:25] [W] [TRT] Weights [name=Conv_8 + Relu_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:25] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:25] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:25] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the wei

[09/22/2022-08:49:26] [W] [TRT] Weights [name=Conv_18 + Relu_19.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:26] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:26] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regulariza

[09/22/2022-08:49:28] [W] [TRT] Weights [name=Conv_24 + Relu_25.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:28] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:29] [W] [TRT] Weights [name=Conv_26 + Add_27 + Relu_28.weight] had the following issues when converted to FP16:
[

...

[09/22/2022-08:49:39] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:39] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:39] [W] [TRT] Weights [name=Conv_78 + Add_79 + Relu_80.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:39] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce th

[09/22/2022-08:49:40] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:40] [W] [TRT] Weights [name=Gemm_88.bias] had the following issues when converted to FP16:
[09/22/2022-08:49:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:41] [W] [TRT] Weights [name=Gemm_88.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/22/2022-08:49:41] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:49:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:41] [W] [TRT] Weights [name=Conv_41 + Add_43 + Relu_44.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:49:41] [W] [TRT] Weights [name=Conv_45 + Relu_46.weight] had the following issues when converted to FP16:
[09/22/2022-08:49:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:49:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-08:49:41] [I] [TRT] Total Host Persistent Memory: 100864
[09/22/2022-08:49:41] [I] [TRT] Total Device Persistent Memory: 75776
[09/22/2022-08:49:41] [I] [TRT] Total Scratch Memory: 0
[09/22/2022-08:49:41] [I] [TRT] [MemUsageStats] Peak memory usage of TRT CPU/GPU memory allocators: CPU 45 MiB, GPU 1131 MiB
[09/22/2022-08:49:41] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 1.38895ms to assign 5 blocks to 58 nodes requiring 2408456 bytes.
[09/22/2022-08:49:41] [I] [TRT] Total Activation Memory: 2408456
[09/22/2022-08:49:41] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in building engine: CPU +40, GPU +43, now: CPU 40, GPU 43 (MiB)
[09/22/2022-08:49:41] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/22/2022-08:49:41] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a

./Flask/Models/resnet34-trt_fp16.plan
./Triton/Models/resnet34-trt_fp16/config.pbtxt
./Triton/Models/resnet34-trt_fp16/1/model.plan


In [7]:
onnx_model = 'resnet34-onnx'
trt_model = 'resnet34-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/resnet34-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/resnet34-trt_int8.plan
[09/22/2022-08:49:45] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:49:45] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:49:45] [I] === Model Options ===
[09/22/2022-08:49:45] [I] Format: ONNX
[09/22/2022-08:49:45] [I] Model: ./Flask/Models/resnet34-onnx.onnx
[09/22/2022-08:49:45] [I] Output:
[09/22/2022-08:49:45] [I] === Build Options ===
[09/22/2022-08:49:45] [I] Max batch: explicit batch
[09/22/2022-08:49:45] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:49:45] [I] minTiming: 1
[09/22/2022-08:49:45] [I] avgTiming: 8
[09/22/2022-08:49:45] [I] Precision: FP32+INT8
[09/22/2022-08:49:45] [I] LayerPrecisions: 
[09/22/2

./Flask/Models/resnet34-trt_int8.plan
./Triton/Models/resnet34-trt_int8/config.pbtxt
./Triton/Models/resnet34-trt_int8/1/model.plan


In [8]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/mobilenet_v2-trt_best.plan
[09/22/2022-08:50:07] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:50:07] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:50:07] [I] === Model Options ===
[09/22/2022-08:50:07] [I] Format: ONNX
[09/22/2022-08:50:07] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/22/2022-08:50:07] [I] Output:
[09/22/2022-08:50:07] [I] === Build Options ===
[09/22/2022-08:50:07] [I] Max batch: explicit batch
[09/22/2022-08:50:07] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:50:07] [I] minTiming: 1
[09/22/2022-08:50:07] [I] avgTiming: 8
[09/22/2022-08:50:07] [I] Precision: FP32+FP16+INT8
[09/22/2022-08:50:07] [I] LayerPrec

[09/22/2022-08:50:28] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:28] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:33] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:33] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:33] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/22/2022-08:50:36] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:36] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:37] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:37] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:37] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/22/2022-08:50:41] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:41] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:41] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:50:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:41] [W] [TRT] If this is not the desired behavior, please modify the

[09/22/2022-08:50:44] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:44] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:50:45] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/22/2022-08:50:45] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:50:45] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

...

[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_84 + PWN(Clip_85).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_84 + PWN(Clip_85).bias] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_84 + PWN(Clip_85).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the w

[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:24] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:24] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:24] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-08:51:26] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:26] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:26] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:26] [W] [TRT] If this is not the desired behavior, please modify the

[09/22/2022-08:51:28] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:51:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:28] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/22/2022-08:51:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:28] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:28] [W] [TRT]  - Subnormal FP16 v

./Flask/Models/mobilenet_v2-trt_best.plan
./Triton/Models/mobilenet_v2-trt_best/config.pbtxt
./Triton/Models/mobilenet_v2-trt_best/1/model.plan


In [9]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/mobilenet_v2-trt_fp16.plan
[09/22/2022-08:51:33] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:51:33] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:51:33] [I] === Model Options ===
[09/22/2022-08:51:33] [I] Format: ONNX
[09/22/2022-08:51:33] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/22/2022-08:51:33] [I] Output:
[09/22/2022-08:51:33] [I] === Build Options ===
[09/22/2022-08:51:33] [I] Max batch: explicit batch
[09/22/2022-08:51:33] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:51:33] [I] minTiming: 1
[09/22/2022-08:51:33] [I] avgTiming: 8
[09/22/2022-08:51:33] [I] Precision: FP32+FP16
[09/22/2022-08:51:33] [I] LayerPrecision

[09/22/2022-08:51:42] [W] [TRT] Weights [name=Conv_0 + PWN(Clip_1).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:42] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:42] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:45] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:45] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:45] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:45] [W] [TRT] Weights [name=Conv_5 + PWN(Clip_6).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:45] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:45] [W] [TRT] If this is not the desired behavior, please modify the weigh

[09/22/2022-08:51:48] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:48] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:48] [W] [TRT] Weights [name=Conv_9.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:48] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:48] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:49] [W] [TRT] Weights [name=Conv_10 + PWN(Clip_11).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:49] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:49] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regular

[09/22/2022-08:51:52] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:52] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:52] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:52] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:52] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:52] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:52] [W] [TRT] Weights [name=Conv_16 + PWN(Clip_17).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:52] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:52] [W] [TRT] If this is not the desired behavior, please modify the

[09/22/2022-08:51:55] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:55] [W] [TRT] Weights [name=Conv_20.weight] had the following issues when converted to FP16:
[09/22/2022-08:51:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:51:55] [W] [TRT] Weights [name=Conv_21 + PWN(Clip_22).weight] had the following issues when converted to FP16:
[09/22/2022-08:51:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:51:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regul

...

[09/22/2022-08:52:28] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:28] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:28] [W] [TRT] Weights [name=Conv_94.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-08:52:29] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/22/2022-08:52:29] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:29] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:29] [W] [TRT] Weights [name=Conv_95 + PWN(Clip_96).weight] had the following issues when converted to FP16:
[09/22/2022-08:52:29] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:29] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:30] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:30] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. 

[09/22/2022-08:52:30] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:30] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:52:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:30] [W] [TRT] Weights [name=Gemm_99.bias] had the following issues when converted to FP16:
[09/22/2022-08:52:30] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:52:30] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:52:30] [W] [TRT] Weights [name=Gemm_99.weight] had the following issues when converted to FP16:
[09/22/2022-08:52:30] [W] [TRT]  - Subnormal FP16 v

[09/22/2022-08:52:31] [I] [TRT] [BlockAssignment] Algorithm ShiftNTopDown took 3.18517ms to assign 5 blocks to 84 nodes requiring 3562500 bytes.
[09/22/2022-08:52:31] [I] [TRT] Total Activation Memory: 3562500
[09/22/2022-08:52:31] [I] [TRT] [MemUsageChange] TensorRT-managed allocation in building engine: CPU +4, GPU +10, now: CPU 4, GPU 10 (MiB)
[09/22/2022-08:52:31] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/22/2022-08:52:31] [W] [TRT] The getMaxBatchSize() function should not be used with an engine built from a network created with NetworkDefinitionCreationFlag::kEXPLICIT_BATCH flag. This function will always return 1.
[09/22/2022-08:52:31] [I] Engine built in 58.3002 sec.
[09/22/2022-08:52:31] [I] [TRT] [MemUsageChange] Init CUDA: CPU +0, GPU +0, now: CPU 1312, GPU 801 (MiB)
[09/22/2022-08:52:31] [I] [TRT] Loaded engine size:

./Flask/Models/mobilenet_v2-trt_fp16.plan
./Triton/Models/mobilenet_v2-trt_fp16/config.pbtxt
./Triton/Models/mobilenet_v2-trt_fp16/1/model.plan


In [10]:
onnx_model = 'mobilenet_v2-onnx'
trt_model = 'mobilenet_v2-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/mobilenet_v2-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/mobilenet_v2-trt_int8.plan
[09/22/2022-08:52:35] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:52:35] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:52:35] [I] === Model Options ===
[09/22/2022-08:52:35] [I] Format: ONNX
[09/22/2022-08:52:35] [I] Model: ./Flask/Models/mobilenet_v2-onnx.onnx
[09/22/2022-08:52:35] [I] Output:
[09/22/2022-08:52:35] [I] === Build Options ===
[09/22/2022-08:52:35] [I] Max batch: explicit batch
[09/22/2022-08:52:35] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:52:35] [I] minTiming: 1
[09/22/2022-08:52:35] [I] avgTiming: 8
[09/22/2022-08:52:35] [I] Precision: FP32+INT8
[09/22/2022-08:52:35] [I] LayerPrecision

[09/22/2022-08:53:25] [I] 
[09/22/2022-08:53:25] [I] === Performance summary ===
[09/22/2022-08:53:25] [I] Throughput: 4760.02 qps
[09/22/2022-08:53:25] [I] Latency: min = 0.235352 ms, max = 0.974701 ms, mean = 0.242911 ms, median = 0.238281 ms, percentile(99%) = 0.457275 ms
[09/22/2022-08:53:25] [I] Enqueue Time: min = 0.138672 ms, max = 0.196045 ms, mean = 0.148237 ms, median = 0.147949 ms, percentile(99%) = 0.1548 ms
[09/22/2022-08:53:25] [I] H2D Latency: min = 0.0307617 ms, max = 0.0493164 ms, mean = 0.0320909 ms, median = 0.0319824 ms, percentile(99%) = 0.0355835 ms
[09/22/2022-08:53:25] [I] GPU Compute Time: min = 0.199646 ms, max = 0.938995 ms, mean = 0.206905 ms, median = 0.202637 ms, percentile(99%) = 0.420898 ms
[09/22/2022-08:53:25] [I] D2H Latency: min = 0.00292969 ms, max = 0.0246582 ms, mean = 0.00390277 ms, median = 0.00366211 ms, percentile(99%) = 0.0057373 ms
[09/22/2022-08:53:25] [I] Total Host Walltime: 3.00104 s
[09/22/2022-08:53:25] [I] Total GPU Compute Time: 2.95

In [11]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b0-trt_best.plan
[09/22/2022-08:53:26] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:53:26] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:53:26] [I] === Model Options ===
[09/22/2022-08:53:26] [I] Format: ONNX
[09/22/2022-08:53:26] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/22/2022-08:53:26] [I] Output:
[09/22/2022-08:53:26] [I] === Build Options ===
[09/22/2022-08:53:26] [I] Max batch: explicit batch
[09/22/2022-08:53:26] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:53:26] [I] minTiming: 1
[09/22/2022-08:53:26] [I] avgTiming: 8
[09/22/2022-08:53:26] [I] Precision: FP32+FP16+INT8
[09/22/2022-08:53:26] [I] 

[09/22/2022-08:55:26] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:26] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:26] [W] [TRT] Weights [name=Conv_27.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:26] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:26] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-08:55:27] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:27] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:27] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:27] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:27] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:27] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:27] [W] [TRT] If thi

[09/22/2022-08:55:38] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:38] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:38] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/22/2022-08:55:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrai

[09/22/2022-08:55:39] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:39] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:39] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:55:39] [W] [TRT] Weights [name=Conv_50 + PWN(PWN(Sigmoid_51), Mul_52).weight] had the following issues when converted to FP16:
[09/22/2022-08:55:39] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:55:39] [W] [TRT] If thi

...

[09/22/2022-08:56:02] [W] [TRT] Weights [name=Conv_219 + PWN(PWN(Sigmoid_220), Mul_221).weight] had the following issues when converted to FP16:
[09/22/2022-08:56:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:02] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:56:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:02] [W] [TRT] Weights [name=Conv_219 + PWN(PWN(Sigmoid_220), Mul_221).weight] had the following issues when converted to FP16:
[09/22/2022-08:56:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:02] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:56:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain wi

[09/22/2022-08:56:02] [W] [TRT] Weights [name=Conv_229.weight] had the following issues when converted to FP16:
[09/22/2022-08:56:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:02] [W] [TRT] Weights [name=Conv_229.weight] had the following issues when converted to FP16:
[09/22/2022-08:56:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:02] [W] [TRT] Weights [name=Conv_229.weight] had the following issues when converted to FP16:
[09/22/2022-08:56:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to

[09/22/2022-08:56:04] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/22/2022-08:56:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:04] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/22/2022-08:56:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:04] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/22/2022-08:56:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:04] [W] [TR

[09/22/2022-08:56:04] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/22/2022-08:56:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:04] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/22/2022-08:56:04] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:04] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:56:05] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/22/2022-08:56:05] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:56:05] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

./Flask/Models/efficientnet_b0-trt_best.plan
./Triton/Models/efficientnet_b0-trt_best/config.pbtxt
./Triton/Models/efficientnet_b0-trt_best/1/model.plan


In [12]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b0-trt_fp16.plan
[09/22/2022-08:56:09] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:56:09] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:56:09] [I] === Model Options ===
[09/22/2022-08:56:09] [I] Format: ONNX
[09/22/2022-08:56:09] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/22/2022-08:56:09] [I] Output:
[09/22/2022-08:56:09] [I] === Build Options ===
[09/22/2022-08:56:09] [I] Max batch: explicit batch
[09/22/2022-08:56:09] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:56:09] [I] minTiming: 1
[09/22/2022-08:56:09] [I] avgTiming: 8
[09/22/2022-08:56:09] [I] Precision: FP32+FP16
[09/22/2022-08:56:09] [I] Layer

[09/22/2022-08:58:03] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:03] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:58:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:03] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:03] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:03] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-08:58:03] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with reg

[09/22/2022-08:58:11] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:11] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:11] [W] [TRT] Weights [name=Conv_28 + PWN(PWN(Sigmoid_29), Mul_30).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:11] [W] [TRT] If thi

[09/22/2022-08:58:17] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:17] [W] [TRT] Weights [name=Conv_35 + PWN(PWN(Sigmoid_36), Mul_37).weight] had the following issues when converted to FP16:
[09/22/2022-08:58:17] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:17] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:20] [W] [TRT] Weights [name=Conv_41 + Add_42.weight] had the following issues when converted to FP16:
[09/22/2022-08:58:20] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:20] [W] [TRT] If this is not the desired b

[09/22/2022-08:58:22] [W] [TRT] Weights [name=Conv_46.weight] had the following issues when converted to FP16:
[09/22/2022-08:58:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:22] [W] [TRT] Weights [name=Conv_46.weight] had the following issues when converted to FP16:
[09/22/2022-08:58:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:58:22] [W] [TRT] Weights [name=Conv_46.weight] had the following issues when converted to FP16:
[09/22/2022-08:58:22] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:58:22] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

...

[09/22/2022-08:59:35] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/22/2022-08:59:35] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:35] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:35] [W] [TRT] Weights [name=Conv_233 + PWN(PWN(Sigmoid_234), Mul_235).weight] had the following issues when converted to FP16:
[09/22/2022-08:59:35] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:35] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired beh

[09/22/2022-08:59:36] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Gemm_238.bias] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Gemm_238.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to r

[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_96.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_99 + Add_100.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_101 + PWN(PWN(Sigmoid_102), Mul_103).weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the 

[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_214.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_217 + Add_218.weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-08:59:36] [W] [TRT] Weights [name=Conv_219 + PWN(PWN(Sigmoid_220), Mul_221).weight] had the following issues when converted to FP16:
[09/22/2022-08:59:36] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-08:59:36] [W] [TRT]  - Values less than smallest positive FP16 Subnormal 

./Flask/Models/efficientnet_b0-trt_fp16.plan
./Triton/Models/efficientnet_b0-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b0-trt_fp16/1/model.plan


In [13]:
onnx_model = 'efficientnet_b0-onnx'
trt_model = 'efficientnet_b0-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 224, 224 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b0-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b0-trt_int8.plan
[09/22/2022-08:59:41] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-08:59:41] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-08:59:41] [I] === Model Options ===
[09/22/2022-08:59:41] [I] Format: ONNX
[09/22/2022-08:59:41] [I] Model: ./Flask/Models/efficientnet_b0-onnx.onnx
[09/22/2022-08:59:41] [I] Output:
[09/22/2022-08:59:41] [I] === Build Options ===
[09/22/2022-08:59:41] [I] Max batch: explicit batch
[09/22/2022-08:59:41] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-08:59:41] [I] minTiming: 1
[09/22/2022-08:59:41] [I] avgTiming: 8
[09/22/2022-08:59:41] [I] Precision: FP32+INT8
[09/22/2022-08:59:41] [I] Layer

./Flask/Models/efficientnet_b0-trt_int8.plan
./Triton/Models/efficientnet_b0-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b0-trt_int8/1/model.plan


In [14]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'best'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --best --saveEngine=./Flask/Models/efficientnet_b7-trt_best.plan
[09/22/2022-09:01:02] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-09:01:02] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-09:01:02] [I] === Model Options ===
[09/22/2022-09:01:02] [I] Format: ONNX
[09/22/2022-09:01:02] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/22/2022-09:01:02] [I] Output:
[09/22/2022-09:01:02] [I] === Build Options ===
[09/22/2022-09:01:02] [I] Max batch: explicit batch
[09/22/2022-09:01:02] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-09:01:02] [I] minTiming: 1
[09/22/2022-09:01:02] [I] avgTiming: 8
[09/22/2022-09:01:02] [I] Precision: FP32+FP16+INT8
[09/22/2022-09:01:02] [I] 

[09/22/2022-09:02:38] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/22/2022-09:02:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:38] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/22/2022-09:02:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:38] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:38] [W] [TRT] Weights [name=Conv_3 + PWN(PWN(Sigmoid_4), Mul_5).weight] had the following issues when converted to FP16:
[09/22/2022-09:02:38] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:38] [W] [TRT] If this is not 

[09/22/2022-09:02:40] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:02:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:40] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/22/2022-09:02:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:40] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:02:40] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:40] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/22/2022-09:02:41] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:02:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:41] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/22/2022-09:02:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:02:41] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:02:41] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:02:41] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/22/2022-09:03:44] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/22/2022-09:03:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:03:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:03:44] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/22/2022-09:03:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:03:44] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:03:44] [W] [TRT] Weights [name=Conv_14 + PWN(PWN(Sigmoid_15), Mul_16).weight] had the following issues when converted to FP16:
[09/22/2022-09:03:44] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:03:44] [W] [TRT] If thi

...

[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_801 + PWN(PWN(Sigmoid_802), Mul_803).weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_804.weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the m

[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_807 + Add_808.weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of t

[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_809 + PWN(PWN(Sigmoid_810), Mul_811).weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:04:55] [W] [TRT] Weights [name=Conv_809 + PWN(PWN(Sigmoid_810), Mul_811).weight] had the following issues when converted to FP16:
[09/22/2022-09:04:55] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:55] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:55] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain wi

[09/22/2022-09:04:57] [W] [TRT] Weights [name=Gemm_814.weight] had the following issues when converted to FP16:
[09/22/2022-09:04:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:04:57] [W] [TRT] Weights [name=Gemm_814.weight] had the following issues when converted to FP16:
[09/22/2022-09:04:57] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:04:57] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:04:57] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2

./Flask/Models/efficientnet_b7-trt_best.plan
./Triton/Models/efficientnet_b7-trt_best/config.pbtxt
./Triton/Models/efficientnet_b7-trt_best/1/model.plan


In [15]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'fp16'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --fp16 --saveEngine=./Flask/Models/efficientnet_b7-trt_fp16.plan
[09/22/2022-09:05:03] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-09:05:03] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-09:05:03] [I] === Model Options ===
[09/22/2022-09:05:03] [I] Format: ONNX
[09/22/2022-09:05:03] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/22/2022-09:05:03] [I] Output:
[09/22/2022-09:05:03] [I] === Build Options ===
[09/22/2022-09:05:03] [I] Max batch: explicit batch
[09/22/2022-09:05:03] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-09:05:03] [I] minTiming: 1
[09/22/2022-09:05:03] [I] avgTiming: 8
[09/22/2022-09:05:03] [I] Precision: FP32+FP16
[09/22/2022-09:05:03] [I] Layer

[09/22/2022-09:05:32] [W] [TRT] Weights [name=Conv_0.weight] had the following issues when converted to FP16:
[09/22/2022-09:05:32] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:05:32] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:06:11] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/22/2022-09:06:11] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:06:11] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:06:12] [W] [TRT] Weights [name=Conv_3.weight] had the following issues when converted to FP16:
[09/22/2022-09:06:12] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:06:12] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduc

[09/22/2022-09:06:21] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:06:21] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:06:21] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:06:21] [W] [TRT] Weights [name=Conv_10.bias] had the following issues when converted to FP16:
[09/22/2022-09:06:21] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:06:21] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:06:21] [W] [TRT] Weights [name=Conv_10.weight] had the following issues when converted to FP16:
[09/22/2022-09:06:21] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:06:21] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

[09/22/2022-09:07:02] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/22/2022-09:07:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:07:02] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/22/2022-09:07:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:07:02] [W] [TRT] Weights [name=Conv_13.weight] had the following issues when converted to FP16:
[09/22/2022-09:07:02] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:02] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-09:07:09] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-09:07:09] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:09] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:07:09] [W] [TRT] Weights [name=Conv_21.bias] had the following issues when converted to FP16:
[09/22/2022-09:07:09] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:09] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:07:09] [W] [TRT] Weights [name=Conv_21.weight] had the following issues when converted to FP16:
[09/22/2022-09:07:09] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:07:09] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to redu

...

[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_610.weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_610.bias] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_613 + Add_614.weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Sub

[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_658 + Add_659.weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_660 + PWN(PWN(Sigmoid_661), Mul_662).weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_735 + PWN(PWN(Sigmoid_736), Mul_737).weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_735 + PWN(PWN(Sigmoid_736), Mul_737).bias] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_738.weight] had the following issues when c

[09/22/2022-09:10:28] [W] [TRT] Weights [name=Conv_792 + Add_793.weight] had the following issues when converted to FP16:
[09/22/2022-09:10:28] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:28] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:28] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to reduce the magnitude of the weights.
[09/22/2022-09:10:29] [W] [TRT] Weights [name=Conv_794 + PWN(PWN(Sigmoid_795), Mul_796).weight] had the following issues when converted to FP16:
[09/22/2022-09:10:29] [W] [TRT]  - Subnormal FP16 values detected. 
[09/22/2022-09:10:29] [W] [TRT]  - Values less than smallest positive FP16 Subnormal value detected. Converting to FP16 minimum subnormalized value. 
[09/22/2022-09:10:29] [W] [TRT] If this is not the desired behavior, please modify the weights or retrain with regularization to re

./Flask/Models/efficientnet_b7-trt_fp16.plan
./Triton/Models/efficientnet_b7-trt_fp16/config.pbtxt
./Triton/Models/efficientnet_b7-trt_fp16/1/model.plan


In [16]:
onnx_model = 'efficientnet_b7-onnx'
trt_model = 'efficientnet_b7-trt'
precision = 'int8'
triton_config = """
platform: "tensorrt_plan"
max_batch_size: 1
input [
 {
    name: "input__0"
    data_type: TYPE_FP32
    format: FORMAT_NCHW
    dims: [ 3, 600, 600 ]
  }
]
output {
    name: "output__0"
    data_type: TYPE_FP32
    dims: [ 1000 ]
  }
"""
save_tensorrt_model(onnx_model, trt_model, precision, triton_config)

&&&& RUNNING TensorRT.trtexec [TensorRT v8402] # trtexec --onnx=./Flask/Models/efficientnet_b7-onnx.onnx --explicitBatch --int8 --saveEngine=./Flask/Models/efficientnet_b7-trt_int8.plan
[09/22/2022-09:10:33] [W] --explicitBatch flag has been deprecated and has no effect!
[09/22/2022-09:10:33] [W] Explicit batch dim is automatically enabled if input model is ONNX or if dynamic shapes are provided when the engine is built.
[09/22/2022-09:10:33] [I] === Model Options ===
[09/22/2022-09:10:33] [I] Format: ONNX
[09/22/2022-09:10:33] [I] Model: ./Flask/Models/efficientnet_b7-onnx.onnx
[09/22/2022-09:10:33] [I] Output:
[09/22/2022-09:10:33] [I] === Build Options ===
[09/22/2022-09:10:33] [I] Max batch: explicit batch
[09/22/2022-09:10:33] [I] Memory Pools: workspace: default, dlaSRAM: default, dlaLocalDRAM: default, dlaGlobalDRAM: default
[09/22/2022-09:10:33] [I] minTiming: 1
[09/22/2022-09:10:33] [I] avgTiming: 8
[09/22/2022-09:10:33] [I] Precision: FP32+INT8
[09/22/2022-09:10:33] [I] Layer

./Flask/Models/efficientnet_b7-trt_int8.plan
./Triton/Models/efficientnet_b7-trt_int8/config.pbtxt
./Triton/Models/efficientnet_b7-trt_int8/1/model.plan
